<a href="https://colab.research.google.com/github/Mondin0/data-eng/blob/main/CEL_Data_Eng_Procesamiento_Ejemplo.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# **Procesamiento de datos**

Veamos que podemos hacer en la etapa de procesamiento sobre diferentes datasets, usando Pandas.

Vamos a usar una serie de datasets, disponibles en Kaggle, que hacen referencia a contenido disponible en plataformas de streaming como Netflix, Amazon Prime y Disney+

- [Netflix dataset](https://www.kaggle.com/datasets/shivamb/netflix-shows)

- [Amazon dataset](https://www.kaggle.com/datasets/shivamb/amazon-prime-movies-and-tv-shows)

- [Disney dataset](https://www.kaggle.com/datasets/shivamb/amazon-prime-movies-and-tv-shows)

*Para ejecutar esta notebook por tu cuenta, tenes que descargar los 3 datasets y, en caso de usar Google Colab, subirlos a la plataforma. Los archivos deben estar en una carpeta `datasets`*

In [ ]:
!pip install -q ydata-profiling

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 356.3/356.3 kB 4.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 102.7/102.7 kB 5.8 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 679.5/679.5 kB 9.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 296.5/296.5 kB 12.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 455.4/455.4 kB 15.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 4.7/4.7 MB 30.7 MB/s eta 0:00:00


In [ ]:
import pandas as pd
from ydata_profiling import ProfileReport

In [ ]:
def load_platform_dataset(path_file, platform_name):
    """
    Carga un archivo CSV que contiene datos
    sobre el contenido disponible en plataformas de streaming.

    Args:
        path_file (str): Ruta al archivo CSV que se va a cargar.
        platform_name (str): Nombre de la plataforma de streaming a la que pertenecen los datos.

    Returns:
        pandas.DataFrame o None: Un DataFrame que contiene los datos del archivo CSV cargado, con una columna
        adicional "platform_name" que indica la plataforma de streaming. En caso de error, se devuelve None.
    """
    try:
        df_platform = pd.read_csv(path_file)
        df_platform["platform_name"] = platform_name
        return df_platform
    except FileNotFoundError:
        print(f"Error: El archivo '{path_file}' no se encontró.")
        return None
    except Exception as e:
        print(f"Error inesperado: {e}")
        return None

In [ ]:
# Vamos a unir todos los datasets en un solo dataframe
platform_names = ["disney_plus", "amazon_prime", "netflix"]
df_platforms = []

for platform in platform_names:
  df_platform = load_platform_dataset(
      f"datasets/{platform}_titles.csv",
      platform)
  df_platforms.append(df_platform)

df_platforms = pd.concat(df_platforms)
df_platforms.head()

show_id     type                                             title  \
0      s1    Movie  Duck the Halls: A Mickey Mouse Christmas Special   
1      s2    Movie                            Ernest Saves Christmas   
2      s3    Movie                      Ice Age: A Mammoth Christmas   
3      s4    Movie                        The Queen Family Singalong   
4      s5  TV Show                             The Beatles: Get Back   

                            director  \
0  Alonso Ramirez Ramos, Dave Wasson   
1                        John Cherry   
2                       Karen Disher   
3                    Hamish Hamilton   
4                                NaN   

                                                cast        country  \
0  Chris Diamantopoulos, Tony Anselmo, Tress MacN...            NaN   
1           Jim Varney, Noelle Parker, Douglas Seale            NaN   
2  Raymond Albert Romano, John Leguizamo, Denis L...  United States   
3  Darren Criss, Adam Lambert, Derek Hough, Alexa...            NaN   
4  John Lennon, Paul McCartney, George Harrison, ...            NaN   

          date_added  release_year rating  duration  \
0  November 26, 2021          2016   TV-G    23 min   
1  November 26, 2021          1988     PG    91 min   
2  November 26, 2021          2011   TV-G    23 min   
3  November 26, 2021          2021  TV-PG    41 min   
4  November 25, 2021          2021    NaN  1 Season   

                       listed_in  \
0              Animation, Family   
1                         Comedy   
2      Animation, Comedy, Family   
3                        Musical   
4  Docuseries, Historical, Music   

                                         description platform_name  
0   Join Mickey and the gang as they duck the halls!   disney_plus  
1  Santa Claus passes his magic bag to a new St. ...   disney_plus  
2          Sid the Sloth is on Santa's naughty list.   disney_plus  
3               This is real life, not just fantasy!   disney_plus  
4  A three-part documentary from Peter Jackson ca...   disney_plus

In [ ]:
# Antes de hacer el procesamiento
# Vamos a inspeccionar el DataFrame
# La siguiente libreria nos da info como la cantidad de nulos, duplicados, etc.
profile = ProfileReport(df_platforms)
profile

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

Habrán visto que hay varias columnas con valores nulos.
En vez de eliminarlos vamos a reemplazarlos con otro valor.

In [ ]:
def fill_null_values(df, column_name, fill_value):
    """
    Rellena los valores nulos en una columna con un valor específico.

    Args:
        df (pd.DataFrame): El DataFrame que contiene los datos.
        column_name (str): El nombre de la columna en la que se deben rellenar los valores nulos.
        fill_value: El valor con el que se deben rellenar los valores nulos en la columna especificada.

    Returns:
        pd.DataFrame: El DataFrame con los valores nulos rellenados en la columna especificada.
    """
    df[column_name] = df[column_name].fillna(fill_value)
    return df

In [ ]:
cols = ["director", "cast", "country", "date_added", "rating"]
values_to_fill = ["N/A", "N/A", "N/A", "1900-01-01", "N/A"]

for col, val in zip(cols, values_to_fill):
  #print(col, val)
  df_platforms = fill_null_values(df_platforms, col, val)

Ahora, prestemos atención a las columnas `director`, `cast`, `listed_in`

In [ ]:
df_platforms[["director", "cast", "listed_in"]].head(15)

director  \
0   Alonso Ramirez Ramos, Dave Wasson   
1                         John Cherry   
2                        Karen Disher   
3                     Hamish Hamilton   
4                                 N/A   
5                          Liz Garbus   
6                                 N/A   
7                                 N/A   
8                                 N/A   
9                    Kirk R. Thatcher   
10                         John Gleim   
11                                N/A   
12                      Leslie Iwerks   
13                                N/A   
14                                N/A   

                                                 cast  \
0   Chris Diamantopoulos, Tony Anselmo, Tress MacN...   
1            Jim Varney, Noelle Parker, Douglas Seale   
2   Raymond Albert Romano, John Leguizamo, Denis L...   
3   Darren Criss, Adam Lambert, Derek Hough, Alexa...   
4   John Lennon, Paul McCartney, George Harrison, ...   
5               Jacques Yves Cousteau, Vincent Cassel   
6   Jeremy Renner, Hailee Steinfeld, Vera Farmiga,...   
7   Gary Muehlberger, Mary Miller, Curly Leach, Sa...   
8   Dr. Ray Ball, Dr. Lauren Smith, Chris Massaro,...   
9   Steve Whitmire, Dave Goelz, Bill Barretta, Eri...   
10  Don Hahn, Kathryn Beaumont, Pete Docter, Kevin...   
11                                                N/A   
12  Stacy Keach, John Lasseter, Brad Bird, John Mu...   
13                  Dr. Michelle Oakley, Zachary Fine   
14                                  Michael B. Jordan   

                                         listed_in  
0                                Animation, Family  
1                                           Comedy  
2                        Animation, Comedy, Family  
3                                          Musical  
4                    Docuseries, Historical, Music  
5                        Biographical, Documentary  
6                      Action-Adventure, Superhero  
7                    Docuseries, Reality, Survival  
8             Animals & Nature, Docuseries, Family  
9                          Comedy, Family, Musical  
10                                     Documentary  
11                           Comedy, Family, Music  
12                             Documentary, Family  
13  Action-Adventure, Animals & Nature, Docuseries  
14                                Animals & Nature

Por ejemplo, una película puede tener diferentes directores, actores (`cast`) o géneros (`listed_in`).
Todos esos valores, en cada campo del dataframe estarán separados por comas. Por ejemplo:
- Animation, Comedy, Family
- Alonso Ramirez Ramos, Dave Wasson
- Jim Varney, Noelle Parker, Douglas Seale.

Lo ideal seria tener una fila para cada uno de estos registros. Si una pelicula tiene 3 generos, debería haber 3 registros con la misma película, una por cada género.

Veamos como lograr eso

In [ ]:
# Primero separamos las columnas necesarias
df_platforms_cast = df_platforms[["show_id", "platform_name", "cast"]].copy()

# Ahora debemos convertir la columna cast a una lista
df_platforms_cast["cast"] = df_platforms_cast["cast"].str.split(", ")

# Por último, separamos los valores para tener una fila por cada actor
df_platforms_cast = df_platforms_cast.explode("cast")
df_platforms_cast.head()

show_id platform_name                  cast
0      s1   disney_plus  Chris Diamantopoulos
0      s1   disney_plus          Tony Anselmo
0      s1   disney_plus       Tress MacNeille
0      s1   disney_plus           Bill Farmer
0      s1   disney_plus          Russi Taylor

Listo! Ya logramos separar esos valores.
Ahora bien, debemos repetir esta operación sobre varias columnas.

In [ ]:
def explode_column(df_origin, cols_to_select, col_to_explode):
    """
    Hacer un "Explode" de una columna con valores separados por comas
    en filas separadas.

    Args:
        df_origin (pd.DataFrame): El DataFrame original.
        cols_to_select (list): Lista de columnas a seleccionar del DF original.
        col_to_explode (str): El nombre de la columna que se va hacer explode.

    Returns:
        pd.DataFrame: Un nuevo DataFrame con las columnas seleccionadas y la columna especificada explotada.
    """
    try:
        df_result = df_origin[cols_to_select].copy()
        df_result[col_to_explode] = df_result[col_to_explode].str.split(", ")
        df_result = df_result.explode(col_to_explode)
        return df_result
    except KeyError as e:
        print(f"Algunas columnas no encontradas en el DataFrame: {e}")
        return None
    except Exception as e:
        print(f"Ha ocurrido un error: {e}")
        return None

In [ ]:
# Probemos la función de nuevo sobre la columna cast
df_platforms_cast = explode_column(
                          df_platforms,
                          ["show_id", "platform_name", "cast"],
                          "cast"
                          )
df_platforms_cast.head()

show_id platform_name                  cast
0      s1   disney_plus  Chris Diamantopoulos
0      s1   disney_plus          Tony Anselmo
0      s1   disney_plus       Tress MacNeille
0      s1   disney_plus           Bill Farmer
0      s1   disney_plus          Russi Taylor

In [ ]:
# Ahora, apliquemos la funcion sobre otras columnas:
# listed_in y directors

df_platforms_listed_in = explode_column(
                          df_platforms,
                          ["show_id", "platform_name", "listed_in"],
                          "listed_in"
)
df_platforms_listed_in.head()

show_id platform_name  listed_in
0      s1   disney_plus  Animation
0      s1   disney_plus     Family
1      s2   disney_plus     Comedy
2      s3   disney_plus  Animation
2      s3   disney_plus     Comedy

In [ ]:
df_platforms_directors = explode_column(
                          df_platforms,
                          ["show_id", "platform_name", "director"],
                          "director"
)
df_platforms_directors.head()

show_id platform_name              director
0      s1   disney_plus  Alonso Ramirez Ramos
0      s1   disney_plus           Dave Wasson
1      s2   disney_plus           John Cherry
2      s3   disney_plus          Karen Disher
3      s4   disney_plus       Hamish Hamilton

Hemos generado 3 dataframes:
- `df_platforms_cast`: Contiene los actores que participan en cada película.
- `df_platforms_directors`: Contiene los directores de cada película.
- `df_platforms_listed_in`: Contiene los géneros asociados a cada película

Con esto, podemos eliminar las columnas `cast`, `director`, `listed_in` del datafrmae *original*, llamado `df_platforms`

In [ ]:
df_platforms = df_platforms.drop(
    columns=["cast", "director", "listed_in"])
df_platforms.head()

show_id     type                                             title  \
0      s1    Movie  Duck the Halls: A Mickey Mouse Christmas Special   
1      s2    Movie                            Ernest Saves Christmas   
2      s3    Movie                      Ice Age: A Mammoth Christmas   
3      s4    Movie                        The Queen Family Singalong   
4      s5  TV Show                             The Beatles: Get Back   

         country         date_added  release_year rating  duration  \
0            N/A  November 26, 2021          2016   TV-G    23 min   
1            N/A  November 26, 2021          1988     PG    91 min   
2  United States  November 26, 2021          2011   TV-G    23 min   
3            N/A  November 26, 2021          2021  TV-PG    41 min   
4            N/A  November 25, 2021          2021    N/A  1 Season   

                                         description platform_name  
0   Join Mickey and the gang as they duck the halls!   disney_plus  
1  Santa Claus passes his magic bag to a new St. ...   disney_plus  
2          Sid the Sloth is on Santa's naughty list.   disney_plus  
3               This is real life, not just fantasy!   disney_plus  
4  A three-part documentary from Peter Jackson ca...   disney_plus

Por último, para finalizar este procesamiento vamos a tratar las columnas de tipo "fecha" *(también llamadas date)*.
Seguramente, sabes que la fecha puede tener distintos formatos. [Acá](https://www.ibm.com/docs/es/cmofm/9.5.0?topic=SSEPCD_9.5.0/com.ibm.ondemand.mp.doc/arsa0257.html) puedes ver algunos ejemplos.

Tenemos que definir el formato de fecha que vamos a aplicar para cada dataset. Por ejemplo, YYYY-MM-DD, primero el año en cuatro digitos, luego el mes en dos digitos y por último día en dos dígitos.

Te invito a leer este [artículo](https://www.programiz.com/python-programming/datetime/strftime) para explorar mas sobre el formateo de fechas en Python

In [ ]:
# Vamos a asegurarnos que el campo date_added
# tenga el formato date
df_platforms.dtypes

show_id          object
type             object
title            object
country          object
date_added       object
release_year      int64
rating           object
duration         object
description      object
platform_name    object
dtype: object

In [ ]:
# Es de tipo object, es decir string
# Vamos a "castearlo"
df_platforms["date_added"] = pd.to_datetime(df_platforms["date_added"])

In [ ]:
# Ahora vamos a formatear la fecha
# con el formato que deseemos
df_platforms["date_added"].dt.strftime("%Y-%m-%d")

0       2021-11-26
1       2021-11-26
2       2021-11-26
3       2021-11-26
4       2021-11-25
           ...    
8802    2019-11-20
8803    2019-07-01
8804    2019-11-01
8805    2020-01-11
8806    2019-03-02
Name: date_added, Length: 19925, dtype: object

In [ ]:
# Probemos otro formato
df_platforms["date_added"].dt.strftime("%d/%m/%Y")

0       26/11/2021
1       26/11/2021
2       26/11/2021
3       26/11/2021
4       25/11/2021
           ...    
8802    20/11/2019
8803    01/07/2019
8804    01/11/2019
8805    11/01/2020
8806    02/03/2019
Name: date_added, Length: 19925, dtype: object

In [ ]:
df_platforms["date_added"] = df_platforms["date_added"].dt.strftime("%Y-%m-%d")

Listo! hemos finalizado el procesamiento.
Nos quedaría guardar los resultados en formato parquet.
¿Te acordás como hacerlo? Te invito a que lo intentes 🧐

In [ ]:
def save_to_parquet():
  """
  ...
  """
  pass

Por último, todo esto debería estar dentro de un solo script para automatizarlo en un futuro. A continuación, podes ver un ejemplo de como quedaría el procesamiento en un solo script.

In [ ]:
import pandas as pd
from ydata_profiling import ProfileReport

def load_platform_dataset(path_file, platform_name):
    """
    Carga un archivo CSV que contiene datos
    sobre el contenido disponible en plataformas de streaming.

    Args:
        path_file (str): Ruta al archivo CSV que se va a cargar.
        platform_name (str): Nombre de la plataforma de streaming a la que pertenecen los datos.

    Returns:
        pandas.DataFrame o None: Un DataFrame que contiene los datos del archivo CSV cargado, con una columna
        adicional "platform_name" que indica la plataforma de streaming. En caso de error, se devuelve None.
    """
    try:
        df_platform = pd.read_csv(path_file)
        df_platform["platform_name"] = platform_name
        return df_platform
    except FileNotFoundError:
        print(f"Error: El archivo '{path_file}' no se encontró.")
        return None
    except Exception as e:
        print(f"Error inesperado: {e}")
        return None

def fill_null_values(df, column_name, fill_value):
    """
    Rellena los valores nulos en una columna con un valor específico.

    Args:
        df (pd.DataFrame): El DataFrame que contiene los datos.
        column_name (str): El nombre de la columna en la que se deben rellenar los valores nulos.
        fill_value: El valor con el que se deben rellenar los valores nulos en la columna especificada.

    Returns:
        pd.DataFrame: El DataFrame con los valores nulos rellenados en la columna especificada.
    """
    df[column_name] = df[column_name].fillna(fill_value)
    return df

def explode_column(df_origin, cols_to_select, col_to_explode):
    """
    Hacer un "Explode" de una columna con valores separados por comas
    en filas separadas.

    Args:
        df_origin (pd.DataFrame): El DataFrame original.
        cols_to_select (list): Lista de columnas a seleccionar del DF original.
        col_to_explode (str): El nombre de la columna que se va hacer explode.

    Returns:
        pd.DataFrame: Un nuevo DataFrame con las columnas seleccionadas y la columna especificada explotada.
    """
    try:
        df_result = df_origin[cols_to_select].copy()
        df_result[col_to_explode] = df_result[col_to_explode].str.split(", ")
        df_result = df_result.explode(col_to_explode)
        return df_result
    except KeyError as e:
        print(f"Algunas columnas no encontradas en el DataFrame: {e}")
        return None
    except Exception as e:
        print(f"Ha ocurrido un error: {e}")
        return None


# Vamos a unir todos los datasets en un solo dataframe
platform_names = ["disney_plus", "amazon_prime", "netflix"]
df_platforms = []

for platform in platform_names:
  df_platform = load_platform_dataset(
      f"datasets/{platform}_titles.csv",
      platform)
  if df_platform is not None:
    df_platforms.append(df_platform)

df_platforms = pd.concat(df_platforms)

# Vamos a rellenar valores nulos
cols = ["director", "cast", "country", "date_added", "rating"]
values_to_fill = ["N/A", "N/A", "N/A", "1900-01-01", "N/A"]

for col, val in zip(cols, values_to_fill):
  #print(col, val)
  df_platforms = fill_null_values(df_platforms, col, val)

# Vamos a hacer explode de algunas columnas
# Probemos la función de nuevo sobre la columna cast
df_platforms_cast = explode_column(
                          df_platforms,
                          ["show_id", "platform_name", "cast"],
                          "cast"
                          )

df_platforms_listed_in = explode_column(
                          df_platforms,
                          ["show_id", "platform_name", "listed_in"],
                          "listed_in"
)

df_platforms_directors = explode_column(
                          df_platforms,
                          ["show_id", "platform_name", "director"],
                          "director"
)

# Generamos nuevos DFs, asi que vamos a borrar
# algunas columnas del DF original
df_platforms = df_platforms.drop(
    columns=["cast", "director", "listed_in"])

# Por ultimo vamos a formatear
# el campo date_added
df_platforms["date_added"] = pd.to_datetime(df_platforms["date_added"])
df_platforms["date_added"] = df_platforms["date_added"].dt.strftime("%Y-%m-%d")

# Listo, solo falta guardar los DFs
# en Parquet o en una base de datos OLAP
# ¿Te animas a hacerlo?